In [1]:
import os, sys
module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)
    
from utils.helpers import launch_env, wrap_env, view_results_ipython
from simulation.gym_duckietown.wrappers import SteeringToWheelVelWrapper
import numpy as np

INFO:aido-protocols:aido-protocols 5.0.5
22:55:26|zn|__init__.py:6|<module>(): zn 2.0.3
22:55:27|zj|__init__.py:5|<module>(): zj 2.0.4
22:55:27|gym-duckietown|__init__.py:10|<module>(): gym-duckietown 2019.0.0

22:55:27|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-small_loop_cw-v0
22:55:27|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-straight_road-v0
22:55:27|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-loop_dyn_duckiebots-v0
22:55:27|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-loop_obstacles-v0
22:55:27|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-zigzag_dists-v0
22:55:27|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-udem1-v0
22:55:27|gym-duckietown|__init__.py:24|reg_map_env(): Registering gym environment id: Duckietown-small_loop

# Control

In robotics, control is often considered a discipline in its own right. Simply, control theory allows us to map from sensory data (or, some sort of intermediate representation) to actuation commands - these commands can help drive our Duckiebot, fly our planes, and even land our rockets.

For those coming from a machine learning background (or those with familiarity with reinforcement learning and imitation learning), you may have noticed a difference between the control covered in class and the controllers, or *policies*, that you may normally train. In robotics, an important part of control is feedback; Feedback allows our controller to self-regulate and tune, and is an important part of the control process. 

In this exercise, we will cover two controllers: a simple, PD controller, and a slightly more complicated pure-pursuit controller in Part 2. 


## Part 1: PID

A PID controller, named for its components of **Proportional**, **Integral**, and **Derivative**, is a simple yet robust mechanism. This generality has lead to its widespread use across multiple disciplines, and is what our exercise will start with. More eloquently (from Wikipedia): *A PID controller continuously calculates an error value e(t) as the difference between a desired setpoint (SP) and a measured process variable (PV) and applies a correction based on proportional, integral, and derivative terms (denoted P, I, and D respectively), hence the name.*

*In practical terms it automatically applies accurate and responsive correction to a control function.*

In our exercise, we will only implement the **P**ropotional and (an approximation to the) **D**erivative control corrections.

Before we begin with the practical portion, the **first part of the exercise** consists of the following:

*Explain, qualitatively, the difference between the three terms. For the following types of controllers, explain the error terms involved in the correction, and what types of applications they are commonly used for. If these controllers do not exist (or cannot), explain why.*

1. P
2. PI
3. PD
4. ID
5. PID

Put your answers inside of the zip file, inside of a file named **03-control.txt**.

***

As we continue towards the practical portion of the first exercise, we will be tasked with setting up a controller that keeps the Duckiebot on the road. 

In the kinematics exercise, we saw how to translate linear and angular velocity commands into wheel rate. After understanding the conversion, we still need to answer a more important question: *what* commands should we use to control the Duckiebot?

Since we're using a simulation, we are able to access the ground-truth values of two variables that are crucial to help our Duckiebot stay in the lane: $d$, the distance to the center of the lane, and $\omega$, the angle with respect to the lane. 

In [2]:
try:
    os.mkdir("sw_assignment_3")
except FileExistsError:
    pass
with open("sw_assignment_3/03-control.txt", "w") as f:
    f.write(
"""Fabrice Normandin. SW assignment #3: Control.

Explain, qualitatively, the difference between the three terms.
- The P term is portional to the error. (K_p e(t))
- the I term uses an accumulation (an integration) of the error term over time (int_{0}^{T}{K_i e(t)})
- The D term is proportional to the change of the error over time (its derivative). (d\dt(K_d e(t)))
1. P:
    P controllers apply a correction that is proportional to the error.
    One example of this (found on Wikipedia) is the float valve inside a toilet reservoir.
    When the water level rises, the lever closes the valve and shuts off the input flow.
    Another example (from https://controlguru.com/the-p-only-control-algorithm/) is a very crude cruise-control system.
    As the speed of the car deviates from the reference value, a correction is applied to the gas intake of the engine, proportion to the error.
    The constant K_p regulates the the magnitude of the response compared to the error.
2. PI:
    Here an additional term is added which uses an integration of the error over time.
    The term has the form k_i \int_{0}^{T} e(t) dt (or also K_i / delta_t * \int_{0}^{T} e(t) dt), with delta_t being the integration timestep length.
    The addition of this term allows the elimination of steady-state error (or offset), which was one of the big limitations of the P controller (https://controlguru.com/pi-control-of-the-heat-exchanger/)
    According to (https://controlstation.com/pi-control/), some of the common uses of the PI controller (which is one of the most commonly used controllers) includes:
    liquid flow control, heat exchanger temperature control, and steam pressure control. 
3. PD:
    Proportional-Derivative controllers include a D term which depends on the change of the error over time.
    In order to avoid having "derivative kick" (https://controlguru.com/pid-control-and-derivative-on-measurement/), the derivative term is
    written as the opposite derivate of the present value, rather than the derivative of the error, which might change abruptly when the target value chanes.
    A common example of this type of controller is the suspension of a car, (as described in http://www.matthewpeterkelly.com/tutorials/pdControl/index.html)
    where the spring exerts a force proportial to the deflection (error), and the damper opposes motion, exerting a force proportional to the change in position of the spring (the derivative of the error) 
4. ID:
    This controller doesn't seem to exist. According to https://robotics.stackexchange.com/questions/2925/why-does-a-id-controller-not-exist?fbclid=IwAR3IkeSSbte1cJrAHUHf3vlw-dXdf6yD0y-VcYRiT62rUpp91X2lXwevKzQ,
    The reason for this is that without a term proportional to the error, there would be no way of knowing if the system is currently in its desired state.
5. PID:
    Here we add both a D and an I term to the P-only controller. The I term tends to augment auscillation in the system, while the D term resists change and provides a dampening effect.
    From my understanding, PID controllers are used pretty much everywhere, in a wide variety of applications. According to Wikipedia,
    the first uses of PID controllers were for automatic steering systems for ships in the 1920's.
""")

In your file `notebooks/code/exercise_03_control/controller.py`, complete function `angle_control_commands`. Update `omega` (angular speed) to achieve your goal while keeping `v` constant.

In [9]:
import numpy as np


class Controller():
    def __init__(self, k_p_dist, k_d_dist, k_p_angle, k_d_angle):
        self.gain = 2.0
        pass
        self.last_dist: float = None
        self.last_angle: float = None
        
        self.k_p_angle = k_p_angle
        self.k_d_angle = k_d_angle
        self.k_p_dist = k_p_dist
        self.k_d_dist = k_d_dist
#         print(self.k_p_dist, self.k_d_dist, self.k_p_angle, self.k_d_angle)

    def angle_control_commands(self, dist, angle):
        # Return the angular velocity in order to control the Duckiebot so that it follows the lane.
        # Parameters:
        #     dist: distance from the center of the lane. Left is negative, right is positive.
        #     angle: angle from the lane direction, in rad. Left is negative, right is positive.
        # Outputs:
        #     omega: angular velocity, in rad/sec. Right is negative, left is positive.
        
        omega = 0. 
        
        #######
        #
        # MODIFY ANGULAR VELOCITY
        #
        # YOUR CODE HERE
        #
        #######
        if self.last_angle is None:
            self.last_angle = angle
        if self.last_dist is None:
            self.last_dist = dist
        
        e_angle = angle
        d_angle = (self.last_angle - angle)

        e_dist = dist
        d_dist = (self.last_dist - dist)
        
        self.last_angle = angle
        self.last_dist = dist
        

        omega += self.k_p_angle * e_angle
        omega += self.k_d_angle * d_angle
        
        omega += self.k_p_dist * e_dist
        omega += self.k_d_dist * d_dist
        return  omega

    def pure_pursuit(self, env, pos, angle, follow_dist=0.25):
        # Return the angular velocity in order to control the Duckiebot using a pure pursuit algorithm.
        # Parameters:
        #     env: Duckietown simulator
        #     pos: global position of the Duckiebot
        #     angle: global angle of the Duckiebot
        # Outputs:
        #     v: linear veloicy in m/s.
        #     omega: angular velocity, in rad/sec. Right is negative, left is positive.
        
        
        closest_curve_point = env.unwrapped.closest_curve_point
        
        # Find the curve point closest to the agent, and the tangent at that point
        closest_point, closest_tangent = closest_curve_point(pos, angle)

        iterations = 0
        
        lookup_distance = follow_dist
        multipler = 0.5
        curve_point = None
        
        while iterations < 10:            
            ########
            #
            #TODO 1: Modify follow_point so that it is a function of closest_point, closest_tangent, and lookup_distance
            #
            ########
            follow_point = closest_point
            
            curve_point, _ = closest_curve_point(follow_point, angle)

            # If we have a valid point on the curve, stop
            if curve_point is not None:
                break

            iterations += 1
            lookup_distance *= multiplier
        ########
        #
        #TODO 2: Modify omega
        #
        ########
        omega = 0.
        v = 0.5

        return v, omega

def try_one_setting(k_p_dist, k_d_dist, k_p_angle, k_d_angle) -> float:
    # Setting up the environment
    local_env = launch_env()
    local_env = SteeringToWheelVelWrapper(wrap_env(local_env))
    local_env.reset()
    local_env.robot_speed = 0.5
    total_reward = 0        
    controller = Controller(k_p_dist, k_d_dist, k_p_angle, k_d_angle)

    # Starting to drive
    for _ in range(1000):
        # Getting the pose
        lane_pose = local_env.get_lane_pos2(local_env.cur_pos, local_env.cur_angle)
        dist = lane_pose.dist        # Distance to lane center. Left is negative, right is positive.
        angle = lane_pose.angle_rad  # Angle from straight, in radians. Left is negative, right is positive.

        # Control
        v = 0.5  # For now, keep linear velocity constant                                                
        omega = controller.angle_control_commands(dist, angle)
        commands = np.array([v, omega])

        # Step
        _, r, d, _ = local_env.step(commands)
        total_reward += r

        if d: 
            print("Duckiebot crashed.")
            break


    local_env.close()
    return total_reward, local_env

import contextlib, io
import dataclasses
from dataclasses import dataclass
import logging
from typing import *
import itertools

logger = logging.getLogger("gym-duckietown")
logging.basicConfig(level="ERROR")

@contextlib.contextmanager
def temporarily_disable_logging(logger):
    start_value = logger.disabled
    logger.disabled = True
    try:
        yield
    except UserWarning:
        pass
    logger.disabled = start_value

@dataclass
class PDControllerParameters():
    k_p_dist: float
    k_d_dist: float
    k_p_angle: float
    k_d_angle: float
        
    def around(self, step_size: float) -> Iterable["PDControllerParameters"]:
        def variants(value):
            return [value, value + step_size, value - step_size]
        parameter_variants = map(variants, list(vars(self).values()))
        for values in itertools.product(*parameter_variants):
            yield PDControllerParameters(*values)

import queue
from queue import PriorityQueue
q = PriorityQueue()
            
# best_params = PDControllerParameters(k_p_dist=10, k_d_dist=0, k_p_angle=10, k_d_angle=0)
# best_reward = 276.39
# best_params = PDControllerParameters(k_p_dist=10, k_d_dist=0, k_p_angle=15.898240000000003, k_d_angle=-33.616)
# best_reward = -1321.7744797146122
# best_params = PDControllerParameters(k_p_dist=10, k_d_dist=10.0, k_p_angle=20.0, k_d_angle=-10.0)
best_params = PDControllerParameters(k_p_dist=10, k_d_dist=-5.0, k_p_angle=20.0, k_d_angle=-5.0)
best_reward = 251.9646409240351
q.put((best_reward, best_params))

print("Current best setting", best_reward, best_params)

step = 0
max_steps = 10
step_size = 10.0
while step < max_steps:
    
    # add or remove to skip the search.
    break
    
    best_reward, best_params = q.get()
    step += 1
    print("Best reward:", best_reward, "best_param:", best_paras)
    for params in best_params.around(step_size):
        with temporarily_disable_logging(logger):
            total_reward, env = try_one_setting(**dataclasses.asdict(params))
        print("\t", params, "\t", total_reward)
        q.put((abs(total_reward), params))
#         if total_reward < best_reward:
#             print("New best setting found")
#             best_reward = total_reward
#             best_params = params
#             local_env = env
#             break
    step_size *= 0.8

with temporarily_disable_logging(logger):
    total_reward, local_env = try_one_setting(**dataclasses.asdict(best_params))
    best_reward = total_reward
print("BEST PARAMETERS FOUND:", best_params, "REWARD:", total_reward)
view_results_ipython(local_env)

Current best setting 251.9646409240351 PDControllerParameters(k_p_dist=10, k_d_dist=-5.0, k_p_angle=20.0, k_d_angle=-5.0)


/usr/local/lib/python3.6/dist-packages/gym/logger.py:30: UserWarning: WARN: Trying to monitor an environment which has no 'spec' set. This usually means you did not create it via 'gym.make', and is recommended only for advanced users.
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


BEST PARAMETERS FOUND: PDControllerParameters(k_p_dist=10, k_d_dist=-5.0, k_p_angle=20.0, k_d_angle=-5.0) REWARD: 247.2487620756103


In [4]:
# from notebooks.code.exercise_03_control.controller import Controller

# Setting up the environment
local_env = launch_env()
local_env = SteeringToWheelVelWrapper(wrap_env(local_env))
local_env.reset()
local_env.robot_speed = 0.5
total_reward = 0        
controller = Controller()
    
# Starting to drive
for _ in range(1000):
    # Getting the pose
    lane_pose = local_env.get_lane_pos2(local_env.cur_pos, local_env.cur_angle)
    dist = lane_pose.dist        # Distance to lane center. Left is negative, right is positive.
    angle = lane_pose.angle_rad  # Angle from straight, in radians. Left is negative, right is positive.
    
    # Control
    v = 0.5  # For now, keep linear velocity constant                                                
    omega = controller.angle_control_commands(dist, angle)
    commands = np.array([v, omega])
    
    # Step
    _, r, d, _ = local_env.step(commands)
    total_reward += r
    
    if d: 
        print("Duckiebot crashed.")
        break
        
        
local_env.close()

22:55:55|gym-duckietown|graphics.py:125|create_frame_buffers(): Falling back to non-multisampled frame buffer
22:55:55|gym-duckietown|graphics.py:125|create_frame_buffers(): Falling back to non-multisampled frame buffer
22:55:55|gym-duckietown|simulator.py:535|_load_map(): loading map file "/duckietown/simulation/gym_duckietown/maps/loop_empty.yaml"
22:55:55|gym-duckietown|simulator.py:1092|_drivable_pos(): [4.13719561 0.         1.88880899] corresponds to tile at (7, 3) which is not drivable: {'coords': (7, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.gym_duckietown.graphics.Texture object at 0x7fe8e88cf198>, 'color': array([1, 1, 1])}
22:55:55|gym-duckietown|simulator.py:1202|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
22:55:55|gym-duckietown|simulator.py:1203|_valid_pose(): safety_factor: 1.3
22:55:55|gym-duckietown|simulator.py:1204|_valid_pose(): pos: [4.0873995 0.        1.9726338]
22:55:55|gym-duckietown|simulator.py:12

22:55:55|gym-duckietown|simulator.py:1202|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
22:55:55|gym-duckietown|simulator.py:1203|_valid_pose(): safety_factor: 1.3
22:55:55|gym-duckietown|simulator.py:1204|_valid_pose(): pos: [3.57292165 0.         1.88314807]
22:55:55|gym-duckietown|simulator.py:1205|_valid_pose(): l_pos: [3.48172154 0.         1.84866924]
22:55:55|gym-duckietown|simulator.py:1206|_valid_pose(): r_pos: [3.66412176 0.         1.91762689]
22:55:55|gym-duckietown|simulator.py:1207|_valid_pose(): f_pos: [3.61429624 0.         1.77370793]
22:55:55|gym-duckietown|simulator.py:1092|_drivable_pos(): [3.50690495 0.         2.23654429] corresponds to tile at (5, 3) which is not drivable: {'coords': (5, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.gym_duckietown.graphics.Texture object at 0x7fe8e88cf198>, 'color': array([1, 1, 1])}
22:55:55|gym-duckietown|simulator.py:1202|_valid_pose(): Invalid pose. Collision free: True

22:55:55|gym-duckietown|simulator.py:1207|_valid_pose(): f_pos: [3.50609039 0.         2.05544313]
22:55:55|gym-duckietown|simulator.py:1092|_drivable_pos(): [4.12972415 0.         2.27350789] corresponds to tile at (7, 3) which is not drivable: {'coords': (7, 3), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.gym_duckietown.graphics.Texture object at 0x7fe8e88cf198>, 'color': array([1, 1, 1])}
22:55:55|gym-duckietown|simulator.py:1202|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
22:55:55|gym-duckietown|simulator.py:1203|_valid_pose(): safety_factor: 1.3
22:55:55|gym-duckietown|simulator.py:1204|_valid_pose(): pos: [4.022444   0.         2.32019802]
22:55:55|gym-duckietown|simulator.py:1205|_valid_pose(): l_pos: [3.98353555 0.         2.23079789]
22:55:55|gym-duckietown|simulator.py:1206|_valid_pose(): r_pos: [4.06135244 0.         2.40959815]
22:55:55|gym-duckietown|simulator.py:1207|_valid_pose(): f_pos: [4.12972415 0.         2.27

22:56:00|gym-duckietown|simulator.py:1092|_drivable_pos(): [2.28873639 0.         2.68406941] corresponds to tile at (3, 4) which is not drivable: {'coords': (3, 4), 'kind': 'floor', 'angle': 0, 'drivable': False, 'texture': <simulation.gym_duckietown.graphics.Texture object at 0x7fe8e88cf198>, 'color': array([1, 1, 1])}
22:56:00|gym-duckietown|simulator.py:1202|_valid_pose(): Invalid pose. Collision free: True On drivable area: False
22:56:00|gym-duckietown|simulator.py:1203|_valid_pose(): safety_factor: 1.3
22:56:00|gym-duckietown|simulator.py:1204|_valid_pose(): pos: [2.38071712 0.         2.71640816]
22:56:00|gym-duckietown|simulator.py:1205|_valid_pose(): l_pos: [2.28873639 0.         2.68406941]
22:56:00|gym-duckietown|simulator.py:1206|_valid_pose(): r_pos: [2.47269785 0.         2.74874692]
22:56:00|gym-duckietown|simulator.py:1207|_valid_pose(): f_pos: [2.41952363 0.         2.60603129]
22:56:00|gym-duckietown|simulator.py:516|reset(): Starting at [2.64153703 0.         2.8846

TypeError: __init__() missing 4 required positional arguments: 'k_p_dist', 'k_d_dist', 'k_p_angle', and 'k_d_angle'

You can see how well you are doing:

In [ ]:
print("Your score: {}".format(total_reward))
print(controller.k_p_dist, controller.k_d_dist, controller.k_p_angle, controller.k_d_angle)
view_results_ipython(local_env)

Within **03-control.txt**, answer the following question:

*Describe the method you used. What kind of controller is it?*

Then, from the list of popular variants of PID controllers, implement a second one. Answer the above question again, and then discuss the differences (both in terms of algorithm and performance) between the two. Do you see any qualitative differences in the driving? Why or why not? Put your answers in **03-control.txt**.

Lastly, for both implementation, plot the **cross-track** error and the **angle error**, and submit the plot(s) (depending on if you decide to separate the metrics on two plots) in the zip file. 

In [ ]:
with open("sw_assignment_3/03-control.txt", "a") as f:
    f.write(
"""
- Describe the method you used. What kind of controller is it?
    I first implemented a simple PD controller, with the following parameters:
        k_p_dist:  constant of the P term w.r.t the dist input
        k_p_angle: constant of the P term w.r.t the angle input
        k_d_dist:  const of the D term w.r.t. the dist input
        k_d_angle: constant of the D term w.r.t. the angle input
    
    Then, I set the derivative parameters `k_d_dist` and `k_d_dist` to zero, effectively converting this model to a P controller.
    
    The values of `k_p_dist` and `k_p_angle` were both set to 10.
    This controller performed pretty well, being able to stay in lane without any significant oscillation. The total_reward was equal to 276.39 with these parameters.

- (Again) Describe the method you used. What kind of controller is it?
    This time, by allowing non-zero values for `k_d_dist` and `k_d_angle`, the above system became a PD controller, rather than a P controller.
    In order to automate this search process, I implemented a simple A* search, which varies the values of each of the four parameters and return the best combination found after a given number of explorations.
    Interestingly, while searching, the reward signal became very negative! For instance:
    
    When using the following parameters: (k_p_dist=10, k_d_dist=0, k_p_angle=15.898240000000003, k_d_angle=-33.616)
    the total reward would be equal to -1321.7744797146122!!!
    After closer inspection, the robot seemed to be jerking constantly on the line, which seems to have provided a negative error value.
    
    Thereafter, I decieded to use the absolute value of the total_reward as the priority index of the A* search algorithm.
    This would therefore search for parameter combinations which give results close to zero.
    
- Discuss the differences (both in terms of algorithm and performance) between the two.
    The PD controller uses an additional term based on the derivative of the error signal (therefore equivalent to the negative derivative of the current value of the input).
    The performance of the PD controller, assuming it is well tuned, performs better than the P controller, 
    because it is able to correct the offset that arises in the P-only controller.
     
- Do you see any qualitative differences in the driving? Why or why not?
    There seems to be a slight difference in terms of driving of the PD and P controllers,
    in that the PD controller is able to respond to sudden turns more smoothly.
    This is consistent with the theory of PD controllers, where the D term is able
    to prevent the overshoot and potential oscillations that can typically occur in P-only controllers.
""")

## Part 2: Pure Pursuit

Within **03-control.txt**, answer the following question:

*While robust, general, and simple, PID controllers also have limitations. What are some failure cases of PID controllers?*
 
In this section, we'll be looking into a type of controller known as a *Pure Pursuit* (PP) controller. A PP controller is not explicitly a reactive controller, but actually requires a reference trajectory that the controller follows. When we input the pose, velocity, and current waypoint, the controller outputs control commands that are used to steer the robot.

Besides robot-specific parameters (which need to be set only once), a PP controller has a single, tunable parameter: *look-ahead* distance. The look-ahead distance is how far along the current path (more on how we do this next section) the robot should _look ahead_ from to compute the angular velocity commands. For simplicity, in our example, the velocity will be fixed.

Before we move on to the code, write the answer to the following in **03-control.txt**:

*Recall the lecture notes about PP controllers. How does the look-ahead distance affect performance? What does a small look-ahead distance prioritize? What about a larger one?*

In [ ]:
with open("sw_assignment_3/03-control.txt", "a") as f:
    f.write(
"""
- While robust, general, and simple, PID controllers also have limitations. What are some failure cases of PID controllers?
    PID controllers can be very difficult to tune properly, given the larger number of parameters compared to P or PD controllers.
    Furthermore, the PID controller has only access to the current value of the error, making it unable to take preventive measures
    to guarantee its stability.

- Recall the lecture notes about PP controllers. How does the look-ahead distance affect performance?
    The look-ahead distance affects the curvature of the robot's instantaneous trajectory.
    
- What does a small look-ahead distance prioritize? What about a larger one?
    A small look-ahead distance prioritizes following the local (fine-grain) structure of the trajectory.
    A large look-ahead distance prioritizes following the global, large-scale trajectory, while perhaps cutting corners.

""")

*** 

As we start the last practical portion of the exercise, we recall a requirement of the PP controller: a reference trajectory. How can we get this from the simulator?

The answer lies inside of the `simulator.py` code, available [here](https://github.com/duckietown/gym-duckietown/blob/master/gym_duckietown/simulator.py). In `gym-duckietown`, we load every tile with a *Bezier* curve, which allows us to calculate a *reward* (useful in reinforcement learning, which we will see later). Each Bezier curve was designed to perfectly fit the right lane of each tile.

`gym-duckietown` provides a few helper functions that we will make use of. Inside of `controller.py:Controller:pure_pursuit`, you will notice a call to `closest_curve_point`, which returns the closest point on the reference trajectory. 

While we have a boilerplate function written, it still needs work. In particular, the main things that need your attention are:

- `follow_point` needs to be a function of a few more items, not just the closest point.
- Once you have the correct waypoint, you need to calculate the $\omega$ that gets you there. You can also change $v$ to go as fast as possible.


In [ ]:
from notebooks.code.exercise_03_control.controller import Controller

# Reset environment
local_env = launch_env()
local_env = SteeringToWheelVelWrapper(wrap_env(local_env))
local_env.reset()
local_env.robot_speed = 0.5
controller = Controller()
total_reward = 0             
    
# Starting to drive
for _ in range(1000):
   
    # Getting the global pose
    pos = local_env.cur_pos
    angle = local_env.cur_angle
    
    # Control
    v, omega = controller.pure_pursuit(local_env, pos, angle)
    commands = np.array([v, omega])
    
    # Step
    _, r, d, _ = local_env.step(commands)
    total_reward += r
    
    if d: 
        print("Duckiebot crashed.")
        break
        
local_env.close()

To see qualitatively how you are doing:

In [ ]:
print("Your score: {}".format(total_reward))
view_results_ipython(local_env)

For this portion of the exercise, submit one plot with **cross-track error**, **angle error**, **commanded linear velocity** and **commanded angular velocity** vs. time. Lastly, experiment with the `lookup_distance` hyperparameter; does the lowering / raising this value match your hypothesis from earlier in this exercise?

Please submit the plot, `controller.py`, and `control.txt` inside of the zip file, and upload it to the Software submission link posted on Piazza.